In [1]:
## Import necessary packages

%matplotlib qt
# On Macs use osx
# For Windows use qt

import numpy as np
from numpy.random import rand
from landscapeWithOcean import LandscapeWithOcean # Import methods from inside file landscapeWithOcean.py

from mpl_toolkits.mplot3d import Axes3D
import matplotlib.pyplot as plt
from matplotlib import cm

In [2]:
plt.rcParams['animation.ffmpeg_path']=r'C:\ffmpeg\bin\ffmpeg.exe'

from matplotlib.animation import FFMpegWriter
metadata = dict(title='Erosion Hawaii', artist='Matplotlib',comment='none')
writer3 = FFMpegWriter(fps=15, metadata=metadata,bitrate=200000)
fig = plt.figure(dpi=200)

In [3]:
def AddHill(Z,NX,NY,xx,yy,r,h):

    for x in range(NX):
        for y in range(NY):
            dx = np.mod(x-xx+NX/2,NX)-NX/2; # difference i-i0 but apply p.b.c. 
            dy = np.mod(y-yy+NY/2,NY)-NY/2;
            dr = np.sqrt(dx**2+dy**2);
            if (dr<r):
                Z[x,y] += h * (np.cos(dr/r*np.pi/2.0))**2;

    return Z

In [4]:
### Define simulation grid and initial conditions

NX = 100 #1000km #number of rows
NY = 100 #1000km #number of columns

d  = 5 # grid spacing in meters
dx = d # keep dx=dy for simplicity
dy = d

LX=NX*dx
LY=NY*dy

# small random features in topography to begin erosion
Z = rand(NX,NY)*0.1

#HAWAIIAN ISLANDS

for i in range(5): #kauai
    xx = 0.8*NX
    yy = 0.2*NY
    r  = (5/50)*NX
    h  = 1600/10 
    Z = AddHill(Z,NX,NY,xx,yy,r,h)
    
for i in range(5): #oahu
    xx = 0.7*NX
    yy = 0.45*NY
    r  = (5/50)*NX
    h  = 1226/10 
    Z = AddHill(Z,NX,NY,xx,yy,r,h)
    
for i in range(5): #maui
    xx = 0.5*NX
    yy = 0.55*NY
    r  = (5/50)*NX
    h  = (3000/10) #peak elevation to scale of x and y bounds, true elevation = h*10 
    Z = AddHill(Z,NX,NY,xx,yy,r,h)
for i in range(5): #maui
    xx = 0.45*NX
    yy = 0.7*NY
    r  = (5/50)*NX
    h  = 3000/10 
    Z = AddHill(Z,NX,NY,xx,yy,r,h)
    
for i in range(5): #big island 
    xx = 0.2*NX
    yy = 0.8*NY
    r  = (10/50)*NX
    h  = 4200/10
    Z = AddHill(Z,NX,NY,xx,yy,r,h)

    
x = np.arange(NX)
y = np.arange(NY)
X,Y = np.meshgrid(y,x) #strange that y goes first !!!
ZMaxOrg = np.max(Z)
#print(ZMaxOrg)

In [5]:
### Physical Parameters
K = 1.0e-5 # meters^(1-2m)/yr

D = 0.01 # m^2/yr

# uplift rate
# uplift = 0.03 / 600.
uplift = 0.0

In [6]:
### Model parameters

# Time step
#dt = d**2 / D / 8. 
dt = d**2 / D /96. #extra small steps 
print(' dt[years] = ',dt)

#Area exponent A^m, default m=1
m=1.3

#gradient exponent g^n, default n=1
n=1.5

#erosion threshold 
theta_c = 10 

 dt[years] =  26.041666666666668


In [7]:
# Total simulation time
T = 10 * 625.0

# total number of iterations
n_iter = int(np.round(T/dt))
print('Number of interation: ',n_iter)

Number of interation:  240


In [8]:
# Initialize landscape 
ls = LandscapeWithOcean(NX,NY)

oceanLevelParameter=0.05  # what does this parameter do?
ls.ComputeOceanVolumeFromOceanLevelParameter(Z,NX,NY,oceanLevelParameter)

ls.pool_check(Z,NX,NY)
ls.A = np.zeros((NX,NY))

Minimum elevation           8.47335862589338e-06
Maximum elevation           2100.0872040084987
Beach level                 105.00436825011562
Ocean volume                844564.2489786252
Percentage of ocean surface 82.64


In [9]:
# Set-up figure
def init_figure():
    fig = plt.figure(figsize=(12.,6.))
    plt.show()
    return fig

def update_figure():
        plt.clf()
        ax1 = fig.add_subplot(121,projection='3d')

        # use equal x-y aspect with an explicit vertical exageration
        vert_exag = 4.
        ax1.set_xlim3d(0,max(NX,NY))
        ax1.set_ylim3d(0,max(NX,NY))
        ax1.set_zlim3d(0,ZMaxOrg)

        ax1.set_title('Surface Relief')

#        surf = ax1.plot_surface(X,Y,Z, cmap = cm.terrain, rstride=1, cstride=1,
#                antialiased=False,linewidth=0)

        ZPlot = np.copy(Z)
        ZPlot[ZPlot<ls.ZBeachLevel] = ls.ZBeachLevel 
        ZPlot -= ls.ZBeachLevel
        ax1.plot_surface(X,Y,ZPlot, cmap = cm.terrain, rstride=1, cstride=1,
                antialiased=False,linewidth=0)

        ax2 = fig.add_subplot(122,aspect='equal')
        ax2.set_title('Elevation')

        #im = ax2.pcolor(Z,cmap=cm.terrain)
        im = ax2.pcolor(ZPlot,cmap=cm.coolwarm)
        cs = ax2.contour(ZPlot,6,colors='k')

        # Add a color bar which maps values to colors.
        cbar = fig.colorbar(im, shrink=0.5, aspect=5)
        # Add the contour line levels to the colorbar
        cbar.add_lines(cs)

        #plt.show()
        plt.draw()
        plt.pause(0.0001)

In [10]:
# Set up figure
fig = init_figure()
update_figure()
Znew = np.copy(Z)

with writer3.saving(fig, "erosion.mp4", dpi=200):
    for it in range(1,n_iter+1):

        ls.calculate_collection_area(Z,NX,NY)
        ls.A *= dx*dy

        for i in range(NX):
            iL = np.mod(i-1,NX) # normally i-1 but observe p.b.c.
            iR = np.mod(i+1,NX) # normally i+1 but observe p.b.c.

            for j in range(NY):
                jD = np.mod(j-1,NY) # normally j-1 but observe p.b.c.
                jU = np.mod(j+1,NY) # normally j+1 but observe p.b.c.

                if ls.ocean[i,j]>0:
                    Psi_z  = 0;
                    Phi_z  = 0;
                else:
                    if ls.drain[i,j]>0: #this cell is a drain
                        s1 = (Z[iR,j]  - Z[iL,j] )/(2.*dx)
                        s2 = (Z[i,jU]  - Z[i,jD] )/(2.*dy)
                        s3 = (Z[iR,jD] - Z[iL,jU])/(2. * np.sqrt( dx**2 + dy**2) )
                        s4 = (Z[iR,jU] - Z[iL,jD])/(2. * np.sqrt( dx**2 + dy**2) )
                        gradient = (np.sqrt(s1**2 + s2**2) + np.sqrt(s3**2 + s4**2))/2.
                        Psi_z = K * ( ls.A[i,j]**m * gradient**n - theta_c)            

                    elif ls.drainage[i,j]>0: #this cell is a drainage point (it drains a pool)

                        if (Z[i,j]>=Z[iR,j]) and ls.pool[iR,j]!=ls.drainage[i,j]: 
                            gradient = (Z[i,j]-Z[iR,j])/dx #pool is on my left, I drain to the right, use this gradiant
                        elif (Z[i,j]>=Z[iL,j]) and ls.pool[iL,j]!=ls.drainage[i,j]:
                            gradient = (Z[i,j]-Z[iL,j])/dx
                        elif (Z[i,j]>=Z[i,jU]) and ls.pool[i,jU]!=ls.drainage[i,j]:
                            gradient = (Z[i,j]-Z[i,jU])/dy
                        elif (Z[i,j]>=Z[i,jD]) and ls.pool[i,jD]!=ls.drainage[i,j]:
                            gradient = (Z[i,j]-Z[i,jD])/dy
                        else:
                            gradient = 0.02 # ??? This does happen (maybe when two pools merge)
                        Psi_z = K * ( ls.A[i,j]**m * gradient**n - theta_c)

                    else: #this cell is a pool, assume it has some mass diffusion but no erosion!
                        Psi_z = 0.

                    if (Psi_z<0):
                        Psi_z = 0. 

                    # diffusion term
                    Phi_z = D * ( (Z[iR,j] - 2.*Z[i,j] + Z[iL,j]) / dx**2 \
                                + (Z[i,jU] - 2.*Z[i,j] + Z[i,jD]) / dx**2 )

                Znew[i,j] = Z[i,j] + (Phi_z - Psi_z + uplift )*dt  

                dZdt= (Znew[i,j] - Z[i,j]) / dt
                CFL = abs(dZdt) * dt / min(dx,dy)
                if (CFL>1.0):
                    print('\nWarning: Time step of',dt,'is probably too large. Safer would be:',dt/CFL)

                if (Znew[i,j]<0.):
                    Znew[i,j] = 0. # yes, this does happen at the boundary when kept at zero

        #Znew[0,:] = 0.0 # resets front boundary to 0
        Z = np.copy(Znew)

        ls.pool_check(Z,NX,NY)

        if (np.mod(it,10)==0): 
            print(it,end='')
            writer3.grab_frame()
            update_figure()
            print(' Ocean level=',ls.ZBeachLevel,' Ocean surface fraction=',100*ls.AOcean/(NX*NY));
        else:
            print('.',end='')
    update_figure()
    print(' Simulation finished.')


In [11]:
#1 
#describe how initial conditions are chosen and what geological features they represent: initial conditions represent 
#the surface such as the min and max elevations representing peaks and troughs, sealevel, where topoograohy is conisdered the beach
#interpretation of oceanlevelparamter in landscapewithocean.py
# self.ZBeachLevel = Zmin+oceanLevelParameter*(Zmax-Zmin) ocean level paramerter is determining what percentage of the total elevation 
#is whith range of the water, so considered the beach or where water is present, the range of the oceans water level 
#how did the geologic features change wiht time?: they eroded and become more flat with time, 
#therefore decreasing the lands surface area by eroding into the ocean and in turn increasing ocean surface area 

In [12]:
#2
#modify code and replace existing intial conditions, make your own landscape  
#erode landscape and generate .mp4 

In [13]:
#3 change K,D,n,m, ocean level, and maybe dt 
#explain how the parameters changed the landscape 

#K is a constant physical parameter that with units of m^(1-2m)/yr. K controls the rate of erodign and also influnces the shape it erodes to 
#D is in units of m^2/yr is the proportioal constant for diffusivity determines the rate it erodes, increasing 
#this value increases the rate of erosion, progresses faster, is also incorated into the dt equation  
#n is the gradient exponent, the gradient controls the slope in terms of z so inrcreasing the exponent chnages
#the influence of the slope of the structure, if n is above 1 the structires slope degrades rapidly 
#m is the area exponent where A is the colelcting area that all water passes through, increasing the expoentn 
#would increase the the influence of the area and changes the shape of the eroded hill to beome more sharp if m is over 1 
#adjusting the ocean level parameter would change what percentage of the total elvation change is influnced by the ocean, establishing ocean elevation 